In [1]:
print("ok")

ok


In [2]:
%pwd

'c:\\Users\\manai\\Desktop\\My Docs\\LLM\\Med-Chatbot\\Final\\Medical-Chatbot\\research'

In [14]:
import os
os.chdir("../")

In [15]:
from langchain.document_loaders import PyPDFLoader, DirectoryLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter

In [16]:
def load_pdf_files(data):
    loader = DirectoryLoader(
        data,
        glob="*.pdf", 
        loader_cls=PyPDFLoader,
        show_progress=True
        )
    
    documents = loader.load()[:637]
    return documents

In [6]:
extracted_data= load_pdf_files("data")

100%|██████████| 1/1 [00:53<00:00, 53.97s/it]

KeyboardInterrupt: 

In [ ]:
extracted_data

[Document(metadata={'producer': 'PDFlib+PDI 6.0.3 (SunOS)', 'creator': 'Adobe Acrobat 6.0', 'creationdate': '2006-10-16T20:19:33+02:00', 'moddate': '2016-02-07T11:23:03+07:00', 'source': 'data\\encyclopedia-of-medicine-vol-1-5-3rd-edition.pdf', 'total_pages': 4505, 'page': 0, 'page_label': 'i'}, page_content=''),
 Document(metadata={'producer': 'PDFlib+PDI 6.0.3 (SunOS)', 'creator': 'Adobe Acrobat 6.0', 'creationdate': '2006-10-16T20:19:33+02:00', 'moddate': '2016-02-07T11:23:03+07:00', 'source': 'data\\encyclopedia-of-medicine-vol-1-5-3rd-edition.pdf', 'total_pages': 4505, 'page': 1, 'page_label': 'ii'}, page_content='The GALE\nENCYCLOPEDIA of\nMEDICINE\nTHIRD EDITION'),
 Document(metadata={'producer': 'PDFlib+PDI 6.0.3 (SunOS)', 'creator': 'Adobe Acrobat 6.0', 'creationdate': '2006-10-16T20:19:33+02:00', 'moddate': '2016-02-07T11:23:03+07:00', 'source': 'data\\encyclopedia-of-medicine-vol-1-5-3rd-edition.pdf', 'total_pages': 4505, 'page': 2, 'page_label': 'iii-1'}, page_content='The 

In [ ]:
len(extracted_data)

637

In [21]:
from typing import List
from langchain.schema import Document

def filter_to_minimal_docs(docs: List[Document]) -> List[Document]:
    minimal_docs : List[Document]= []
    for doc in docs:
        source = doc.metadata.get("source")
        minimal_docs.append(
            Document(
                page_content=doc.page_content,
                metadata={
                    "source": source}))
    return minimal_docs

In [18]:
minimal_docs = filter_to_minimal_docs(extracted_data)

NameError: name 'extracted_data' is not defined

In [ ]:
minimal_docs

[Document(metadata={'source': 'data\\encyclopedia-of-medicine-vol-1-5-3rd-edition.pdf'}, page_content=''),
 Document(metadata={'source': 'data\\encyclopedia-of-medicine-vol-1-5-3rd-edition.pdf'}, page_content='The GALE\nENCYCLOPEDIA of\nMEDICINE\nTHIRD EDITION'),
 Document(metadata={'source': 'data\\encyclopedia-of-medicine-vol-1-5-3rd-edition.pdf'}, page_content='The GALE\nENCYCLOPEDIA of\nMEDICINE\nTHIRD EDITION\nVOLUME\n\x81\n1\nA-B\nJACQUELINE L. LONGE, PROJECT EDITOR'),
 Document(metadata={'source': 'data\\encyclopedia-of-medicine-vol-1-5-3rd-edition.pdf'}, page_content='The GALE\nENCYCLOPEDIA of\nMEDICINE\nTHIRD EDITION\nVOLUME\n\x81\n2\nC-F\nJACQUELINE L. LONGE, PROJECT EDITOR'),
 Document(metadata={'source': 'data\\encyclopedia-of-medicine-vol-1-5-3rd-edition.pdf'}, page_content='The GALE\nENCYCLOPEDIA of\nMEDICINE\nTHIRD EDITION\nVOLUME\n\x81\n3\nG-M\nJACQUELINE L. LONGE, PROJECT EDITOR'),
 Document(metadata={'source': 'data\\encyclopedia-of-medicine-vol-1-5-3rd-edition.pdf'},

In [19]:
def text_splitter(minimal_docs):
    text_splitter = RecursiveCharacterTextSplitter(
        chunk_size=500,
        chunk_overlap=20
        )
    text_chunks=text_splitter.split_documents(minimal_docs)
    return text_chunks

In [20]:
text_chunks = text_splitter(minimal_docs)

print(len(text_chunks))

NameError: name 'minimal_docs' is not defined

In [22]:
from langchain.embeddings import HuggingFaceEmbeddings

def download_embeddings():

    model_name = "sentence-transformers/all-MiniLM-L6-v2"
    embeddings= HuggingFaceEmbeddings(
        model_name=model_name,
       
    )
    return embeddings
embeddings = download_embeddings()

In [ ]:
embeddings

HuggingFaceEmbeddings(client=SentenceTransformer(
  (0): Transformer({'max_seq_length': 256, 'do_lower_case': False}) with Transformer model: BertModel 
  (1): Pooling({'word_embedding_dimension': 384, 'pooling_mode_cls_token': False, 'pooling_mode_mean_tokens': True, 'pooling_mode_max_tokens': False, 'pooling_mode_mean_sqrt_len_tokens': False, 'pooling_mode_weightedmean_tokens': False, 'pooling_mode_lasttoken': False, 'include_prompt': True})
  (2): Normalize()
), model_name='sentence-transformers/all-MiniLM-L6-v2', cache_folder=None, model_kwargs={}, encode_kwargs={}, multi_process=False, show_progress=False)

In [23]:
vector=embeddings.embed_query("What is the purpose of this study?")
vector

[0.0017421446973457932,
 0.12773600220680237,
 0.004604978486895561,
 0.08658654242753983,
 0.03266902640461922,
 0.0227113738656044,
 0.019731057807803154,
 0.03991053253412247,
 0.002750018145889044,
 0.0013382162433117628,
 0.017413897439837456,
 0.012651468627154827,
 -0.06868179887533188,
 -0.021862203255295753,
 -0.1120699867606163,
 -0.03444591537117958,
 -0.03633436933159828,
 -0.04302364960312843,
 -0.014407933689653873,
 -0.0066823819652199745,
 -0.035310566425323486,
 0.006849474739283323,
 0.11979883909225464,
 0.004998945165425539,
 -0.06026788800954819,
 0.03437516838312149,
 -0.015030037611722946,
 -0.01880381442606449,
 0.052385710179805756,
 0.011559675447642803,
 0.06434395909309387,
 0.13303741812705994,
 0.07992512732744217,
 0.05266702175140381,
 -0.05915122851729393,
 0.042774319648742676,
 0.012336930260062218,
 0.04985865205526352,
 -0.0046969871036708355,
 0.04913445934653282,
 -0.03408896550536156,
 -0.04048291966319084,
 0.024382222443819046,
 0.0061912965029

In [67]:
from dotenv import load_dotenv
load_dotenv()
import os

In [69]:
Pinecone_API_KEY = os.getenv("Pinecone_API_KEY")
OpenAI_API_KEY = os.getenv("OpenAI_API_KEY")
HUGGINGFACEHUB_API_KEY = os.getenv("HUGGINGFACEHUB_API_KEY")

os.environ["PINECONE_API_KEY"] = Pinecone_API_KEY
os.environ["OPENAI_API_KEY"] = OpenAI_API_KEY
os.environ["HUGGINGFACEHUB_API_KEY"] = HUGGINGFACEHUB_API_KEY

TypeError: str expected, not NoneType

In [ ]:
Hugg

In [26]:
from pinecone import Pinecone
pinecone_API_key=Pinecone_API_KEY

pc = Pinecone(api_key=pinecone_API_key)

In [11]:
pc

In [27]:
from pinecone import ServerlessSpec

index_name = "medical-chatbot"

if not pc.has_index(index_name):
    pc.create_index(
        name=index_name,
        dimension=384,
        metric="cosine",
        spec=ServerlessSpec(
            cloud="aws",
            region="us-east-1"
        ))
index = pc.Index(index_name)    
    


In [ ]:
#Storing vectors into pinecone


from langchain_pinecone import PineconeVectorStore

docssearch=PineconeVectorStore.from_documents(
    documents=text_chunks,
    embedding=embeddings,
    index_name=index_name
    
)

NameError: name 'text_chunks' is not defined

In [ ]:
#loading existing index(data in the db) from pinecone

from langchain_pinecone import PineconeVectorStore

docsearch=PineconeVectorStore.from_existing_index(
    index_name=index_name,
    embedding=embeddings
)

# Add more data to existing index in pinecone


In [29]:
dswith = Document(
    page_content="Adding more data to the existing index in Pinecone.",
    metadata={
        "source": "Myself"
    }
)

In [30]:
docsearch.add_documents(documents=[dswith])

['e565ff0a-69c4-4ad7-8f6f-c2f92f1456d5']

# Retrieving

In [31]:
retriever= docsearch.as_retriever(
    search_type="similarity",
    search_kwargs={
        "k": 3
    }
)

In [33]:
retrieved_docs= retriever.invoke("What is acne?")
retrieved_docs

[Document(id='77aa7726-3e3f-4ea8-a96d-ce69f9edb92a', metadata={'source': 'data\\encyclopedia-of-medicine-vol-1-5-3rd-edition.pdf'}, page_content='Researchers, Inc. Reproduced by permission.)\n26 GALE ENCYCLOPEDIA OF MEDICINE\nAcne'),
 Document(id='feee8aef-f54b-4ea6-b205-8919199ad568', metadata={'source': 'data\\encyclopedia-of-medicine-vol-1-5-3rd-edition.pdf'}, page_content='Sebaceous follicles— A structure found within the\nskin that houses the oil-producing glands and hair\nfollicles, where pimples form.\nSebum— An oily skin moisturizer produced by\nsebaceous glands.\nTretinoin— A drug that works by increasing the\nturnover (death and replacement) of skin cells.\nAcne vulgaris affecting a woman’s face. Acne is the general\nname given to a skin disorder in which the sebaceous glands\nbecome inflamed. (Photograph by Biophoto Associates, Photo'),
 Document(id='c7bcf54d-a4e9-4e93-8377-010a40098330', metadata={'source': 'data\\encyclopedia-of-medicine-vol-1-5-3rd-edition.pdf'}, page_con

In [41]:
from langchain_openai import ChatOpenAI

chat_model = ChatOpenAI( model="gpt-3.5-turbo")

In [42]:
from langchain.chains import create_retrieval_chain
from langchain.chains.combine_documents import create_stuff_documents_chain
from langchain_core.prompts import ChatPromptTemplate

In [43]:
system_prompt=(
    "Your are a medical assistant to help the user with their medical queries, diagnosis on the basis of symptoms, and prescription of medicines. "
    "Use the following pieces of retrieved context to answer the questions. if you don't know the answer, just say that you don't know, don't try to make up an answer. Use three sentences maximun and keep the naswer concise"
    "\n \n"
    "{context}"
)

prompt= ChatPromptTemplate.from_messages(
    [
        ("system", system_prompt),
        ("human", "{input}")
    ]
)

In [44]:
question_answer_chain = create_stuff_documents_chain(chat_model, prompt)
rag_chain = create_retrieval_chain(retriever, question_answer_chain)

In [45]:
response= rag_chain.invoke({"input": "What is acne?"})
print(response["answer"])

RateLimitError: Error code: 429 - {'error': {'message': 'You exceeded your current quota, please check your plan and billing details. For more information on this error, read the docs: https://platform.openai.com/docs/guides/error-codes/api-errors.', 'type': 'insufficient_quota', 'param': None, 'code': 'insufficient_quota'}}